<b> Single-cell analysis </b> 

Performing a statistical analysis on some data we typically have to understand the balance between the number of features and number of observations

In the case of single-cell analysis, the number of observations is higher than the number of features. 

The goal of single-cell analysis is to discover novel cell popultation. Hence, we can refer it to unsupervised analysis.


We will use autoencoder to perform dimensional reduction of rna_scale dataset. Then group it to different type of cell(clustering)


In [1]:
%reload_ext autoreload
%autoreload 2
%matplotlib inline

In [2]:
import pandas as pd
import numpy as np
import torch
import torch.nn as nn
from torch.utils.data import DataLoader
from sklearn.model_selection import train_test_split
from pathlib import Path

from learn.dataset import TabularDataset
from learn.train import train_model, get_encodings

import umap
import plotly.express as px
import plotly.graph_objects as go

In [3]:
rna = pd.read_csv("C:/Users/super/OneDrive - The University of Tokyo/Bioinformatic intenship/citeseq_autoencoder-master/data/protein_scale.csv.gz", index_col=0).T
rna = rna.reset_index(drop=True)
rna.head()

CD11a     CD11c     CD123  CD127-IL7Ra      CD14      CD16     CD161  \
0 -1.849174 -0.372667 -0.072177    -0.634849 -0.464785  0.207650 -0.005108   
1  0.343613 -1.012818 -0.474588     1.776928 -0.672261 -0.152689  5.036511   
2 -0.829742 -0.847536 -0.675120     0.705449 -0.654620 -0.427962 -0.443269   
3  0.157304 -0.601292 -0.558123     0.758353 -0.660516 -0.384782  0.052340   
4  1.606986  1.762460  0.264567    -0.918552  2.004037 -0.497364 -0.392328   

       CD19  CD197-CCR7      CD25  ...      CD38       CD4    CD45RA  \
0 -0.361779    0.691453  0.492961  ...  1.046025 -0.578292 -0.685804   
1 -0.352564   -1.541172 -0.942280  ... -0.665740  1.435716 -1.205478   
2 -0.478648   -0.552103 -1.208599  ...  0.010368  1.745735  0.426769   
3 -0.413611   -0.338678 -0.098834  ... -0.202340  1.596914 -1.300920   
4 -0.327233   -0.539660 -0.375834  ...  1.264582 -0.308044 -1.246741   

     CD45RO      CD56      CD57      CD69     CD79b      CD8a    HLA.DR  
0 -0.618250  0.486534  1.084345  0.114363 -0.279477 -0.474619  0.998738  
1  0.359657  2.607521 -0.612902 -1.146097  0.245467 -0.762164 -0.838409  
2 -1.072402 -0.223553  1.059687 -0.635409 -0.844739 -0.448139 -1.074838  
3  2.089684 -0.637078 -0.166773 -0.541819 -0.646660 -0.663541 -0.589663  
4  0.639829 -0.511057  0.300100  1.660178 -0.351614 -0.581021  0.766440  

[5 rows x 25 columns]

In [4]:
nfeatures = rna.shape[1]
nfeatures
train, valid = train_test_split(rna.to_numpy(dtype=np.float32), test_size=0.1, random_state=0)
train.shape, valid.shape
train_ds = TabularDataset(train)
valid_ds = TabularDataset(valid)
#load data
train_dl = DataLoader(train_ds, batch_size=64, shuffle=True)
valid_dl = DataLoader(valid_ds, batch_size=64, shuffle=False)

In [5]:
x, y = next(iter(train_dl))
x.shape, y.shape

(torch.Size([64, 25]), torch.Size([64, 25]))

In [6]:
# Generate Autoencoder Model(Modify from CiteAutoencoder model)
import torch
import torch.nn as nn


class LinBnDrop(nn.Sequential):
    """Module grouping `BatchNorm1d`, `Dropout` and `Linear` layers, adapted from fastai."""
    
    def __init__(self, n_in, n_out, bn=True, p=0., act=None, lin_first=True):
        layers = [nn.BatchNorm1d(n_out if lin_first else n_in)] if bn else []
        if p != 0: layers.append(nn.Dropout(p))
        lin = [nn.Linear(n_in, n_out, bias=not bn)]
        if act is not None: lin.append(act)
        layers = lin+layers if lin_first else layers+lin
        super().__init__(*layers)


class Encoder(nn.Module):
    """Encoder for CITE-seq data"""
    
    def __init__(self, nfeatures_rna, nfeatures_pro, hidden_rna, hidden_pro, z_dim):
        super().__init__()
        self.nfeatures_rna = nfeatures_rna
        self.nfeatures_pro = nfeatures_pro

        if nfeatures_rna > 0:
            self.encoder_rna = LinBnDrop(nfeatures_rna, hidden_rna, p=0.1, act=nn.LeakyReLU())

        if nfeatures_pro > 0:
            self.encoder_protein = LinBnDrop(nfeatures_pro, hidden_pro, p=0.1, act=nn.LeakyReLU())

        # make sure hidden_rna and hidden_pro are set correctly
        hidden_rna = 0 if nfeatures_rna == 0 else hidden_rna
        hidden_pro = 0 if nfeatures_pro == 0 else hidden_pro
        
        self.encoder = LinBnDrop(hidden_rna + hidden_pro, z_dim, act=nn.LeakyReLU())

    def forward(self, x):
        if self.nfeatures_rna > 0 and self.nfeatures_pro > 0:
            x_rna = self.encoder_rna(x[:, :self.nfeatures_rna])
            x_pro = self.encoder_protein(x[:, self.nfeatures_rna:])
            x = torch.cat([x_rna, x_pro], 1)

        elif self.nfeatures_rna > 0 and self.nfeatures_pro == 0:
            x = self.encoder_rna(x)

        elif self.nfeatures_rna == 0 and self.nfeatures_pro > 0:
            x = self.encoder_protein(x)
            
        return self.encoder(x)


class Decoder(nn.Module):
    """Decoder for CITE-seq data"""
    def __init__(self, nfeatures_rna, nfeatures_pro, hidden_rna, hidden_pro, z_dim):
        super().__init__()
        self.nfeatures_rna = nfeatures_rna
        self.nfeatures_pro = nfeatures_pro

        # make sure hidden_rna and hidden_pro are set correctly
        hidden_rna = 0 if nfeatures_rna == 0 else hidden_rna
        hidden_pro = 0 if nfeatures_pro == 0 else hidden_pro

        hidden = hidden_rna + hidden_pro

        self.decoder = nn.Sequential(
            LinBnDrop(z_dim, hidden, act=nn.LeakyReLU()),
            LinBnDrop(hidden, nfeatures_rna + nfeatures_pro, bn=False)
            )

    def forward(self, x):
        x = self.decoder(x)
        return x

class CiteAutoencoder(nn.Module):
    def __init__(self, nfeatures_rna=0, nfeatures_pro=0, hidden_rna=120, hidden_pro=8, z_dim=20):
        """ Autoencoder for citeseq data """
        super().__init__()
 
        self.encoder = Encoder(nfeatures_rna, nfeatures_pro, hidden_rna, hidden_pro, z_dim)
        self.decoder = Decoder(nfeatures_rna, nfeatures_pro, hidden_rna, hidden_pro, z_dim)


    def forward(self, x):
        x = self.encoder(x)
        x = self.decoder(x)
        return x

In [7]:
model = CiteAutoencoder(nfeatures_rna=nfeatures, nfeatures_pro=0, hidden_rna=100, hidden_pro=0, z_dim=20)

In [8]:
model(x).shape

torch.Size([64, 25])

In [9]:
# Train the data 
lr = 1e-2
epochs = 50
model, losses = train_model(model, train_dl, valid_dl, lr=lr, epochs=epochs)

 20%|██████████████████████████████▏                                                                                                                        | 10/50 [00:11<00:46,  1.17s/it]

Epoch 10: train loss 0.06405248100615778; valid loss 0.02865889537569519


 40%|████████████████████████████████████████████████████████████▍                                                                                          | 20/50 [00:24<00:39,  1.33s/it]

Epoch 20: train loss 0.057966634282433906; valid loss 0.02039190201329206


 60%|██████████████████████████████████████████████████████████████████████████████████████████▌                                                            | 30/50 [00:39<00:32,  1.63s/it]

Epoch 30: train loss 0.05330355368460664; valid loss 0.017427874124345443


 80%|████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████▊                              | 40/50 [00:57<00:17,  1.70s/it]

Epoch 40: train loss 0.04729067390076649; valid loss 0.014905202719765427


100%|███████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████████| 50/50 [01:15<00:00,  1.50s/it]

Epoch 50: train loss 0.044979420832133334; valid loss 0.01268958869709535


In [ ]:
# plot the figure to show the cell 

In [10]:
fig = go.Figure()
fig.add_trace(go.Scatter(x=np.arange(1, epochs+1, 1), y=losses['train'],
                         mode='lines',
                         name='train'))
fig.add_trace(go.Scatter(x=np.arange(1, epochs+1, 1), y=losses['valid'],
                         mode='lines',
                         name='valid'))
fig.show()

In [11]:
test_ds = TabularDataset(rna.to_numpy(dtype=np.float32))
test_dl = DataLoader(test_ds, batch_size=64, shuffle=False)

encodings = get_encodings(model, test_dl)
encodings = encodings.cpu().numpy()
encodings.shape

(30672, 20)

In [12]:
# annotations
metadata = pd.read_csv("C:/Users/super/OneDrive - The University of Tokyo/Bioinformatic intenship/citeseq_autoencoder-master/data/metadata.csv.gz", index_col=0)
metadata.head()

orig.ident  nCount_RNA  nFeature_RNA  nCount_ADT  \
a_AAACCTGAGCTTATCG-1     bmcite        7546          2136        1350   
a_AAACCTGAGGTGGGTT-1     bmcite        1029           437        2970   
a_AAACCTGAGTACATGA-1     bmcite        1111           429        2474   
a_AAACCTGCAAACCTAC-1     bmcite        2741           851        4799   
a_AAACCTGCAAGGTGTG-1     bmcite        2099           843        5434   

                      nFeature_ADT       lane   donor       celltype.l1  \
a_AAACCTGAGCTTATCG-1            25  HumanHTO4  batch1  Progenitor cells   
a_AAACCTGAGGTGGGTT-1            25  HumanHTO1  batch1            T cell   
a_AAACCTGAGTACATGA-1            23  HumanHTO5  batch1            T cell   
a_AAACCTGCAAACCTAC-1            25  HumanHTO3  batch1            T cell   
a_AAACCTGCAAGGTGTG-1            25  HumanHTO2  batch1           Mono/DC   

                     celltype.l2  RNA.weight  ADT.weight  wsnn_res.2  \
a_AAACCTGAGCTTATCG-1    Prog_RBC    0.487299    0.512701          19   
a_AAACCTGAGGTGGGTT-1         gdT    0.245543    0.754457          10   
a_AAACCTGAGTACATGA-1   CD4 Naive    0.501680    0.498320           1   
a_AAACCTGCAAACCTAC-1  CD4 Memory    0.431308    0.568692           4   
a_AAACCTGCAAGGTGTG-1   CD14 Mono    0.572097    0.427903           2   

                      seurat_clusters  
a_AAACCTGAGCTTATCG-1               19  
a_AAACCTGAGGTGGGTT-1               10  
a_AAACCTGAGTACATGA-1                1  
a_AAACCTGCAAACCTAC-1                4  
a_AAACCTGCAAGGTGTG-1                2

In [13]:
metadata.shape

(30672, 13)

In [14]:
# separate CD4 and CD8 in l1
metadata["celltype.l1.5"] = metadata["celltype.l1"].values
metadata.loc[metadata["celltype.l2"].str.startswith("CD4"), "celltype.l1.5"] = "CD4 T"
metadata.loc[metadata["celltype.l2"].str.startswith("CD8"), "celltype.l1.5"] = "CD8 T"

In [15]:
# Prepare data for visualization
embedding = umap.UMAP(random_state=0).fit_transform(encodings)

In [16]:
plot_df = metadata.copy()
plot_df["UMAP1"] = embedding[:, 0]
plot_df["UMAP2"] = embedding[:, 1]

In [17]:
fig = px.scatter(plot_df, x="UMAP1", y="UMAP2", color="celltype.l1.5")
fig.show()

We see that grouped data above for specific type of cell